In [ ]:
#import necessary packages
%matplotlib qt
import numpy as np
from numpy.random import rand

import matplotlib.pyplot as plt
import matplotlib as mpl
from matplotlib.ticker import MaxNLocator

# !pip install svgpath2mpl
# !pip install svgpathtools
from svgpathtools import svg2paths
from svgpath2mpl import parse_path

import math

from matplotlib.animation import FFMpegWriter
metadata = dict(title='Final_Project', artist='CW_JUNG',
                comment='An attempt to simulate fluid dynamics in a tesla valve using python')
writer = FFMpegWriter(fps=15, metadata=metadata)

In [ ]:
#custom markers for rock,scissor,paper
r, att_r = svg2paths('rock.svg')
s, att_s = svg2paths('scissor.svg')
p, att_p = svg2paths('paper.svg')
sp, att_sp = svg2paths('trek.svg')
l, att_l = svg2paths('lizard.svg')

In [ ]:
#fine tune markers
rock_marker = parse_path(att_r[0]['d'])
rock_marker = rock_marker.transformed(mpl.transforms.Affine2D().rotate_deg(180))
rock_marker.vertices -= rock_marker.vertices.mean(axis=0)

scissor_marker = parse_path(att_s[0]['d'])
scissor_marker = scissor_marker.transformed(mpl.transforms.Affine2D().rotate_deg(90))
scissor_marker.vertices -= scissor_marker.vertices.mean(axis=0)
                                                    
paper_marker = parse_path(att_p[0]['d'])
paper_marker = paper_marker.transformed(mpl.transforms.Affine2D().rotate_deg(180))
paper_marker.vertices -= paper_marker.vertices.mean(axis=0)

spock_marker = parse_path(att_sp[0]['d'])
spock_marker = spock_marker.transformed(mpl.transforms.Affine2D().rotate_deg(180))
spock_marker.vertices -= spock_marker.vertices.mean(axis=0)

lizard_marker = parse_path(att_l[0]['d'])
lizard_marker = lizard_marker.transformed(mpl.transforms.Affine2D().rotate_deg(180))
lizard_marker.vertices -= lizard_marker.vertices.mean(axis=0)

In [ ]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(4,7))
    return fig

def display(mass, mode = 3):
    rock = []
    scissor = []
    paper = []
    spock = []
    lizard = []
    
    for el in mass:
        if el[2] == 0:
            rock.append(el)
        elif el[2] == 1:
            scissor.append(el)
        elif el[2] == 2:
            paper.append(el)
        
        if mode == 5:
            if el[2] == 3:
                spock.append(el)
            elif el[2] == 4:
                lizard.append(el)
        
    
    plt.clf()
    ax1 = fig.add_subplot(211)
    
    players = ['Rock', 'Scissor', 'Paper']
    counts = [len(rock), len(scissor), len(paper)]
    bar_colors = ['tab:gray', 'tab:red', 'tab:blue']
    
    if mode == 5:
        players = ['Rock', 'Scissor', 'Paper', 'Spock', 'Lizard']
        counts = [len(rock), len(scissor), len(paper), len(spock), len(lizard)]
        bar_colors = ['tab:gray', 'tab:red', 'tab:blue', 'tab:brown', 'tab:green']
    
    ax1.bar(players, counts, color=bar_colors)
    ax1.set_ylabel('Element Counts')
    ax1.set_title('Which element is winning?')
    ax1.grid('on', axis='y')
    ax1.yaxis.set_major_locator(MaxNLocator(integer=True))
    
    ax2 = fig.add_subplot(212)
    
    for loc in rock:
        ax2.plot(loc[0], loc[1], marker=rock_marker, markersize = 5, color = 'gray')
        
    for loc in scissor:
        ax2.plot(loc[0], loc[1], marker=scissor_marker, markersize = 8, color = 'red')
        
    for loc in paper:
        ax2.plot(loc[0], loc[1], marker=paper_marker, markersize = 8, color = 'blue')
        
    if mode == 5:
        for loc in spock:
            ax2.plot(loc[0], loc[1], marker=spock_marker, markersize = 8, color = 'brown')
        
        for loc in lizard:
            ax2.plot(loc[0], loc[1], marker=lizard_marker, markersize = 8, color = 'green')
    
    plt.xlim(-50,50)
    plt.ylim(-50,50)
    
    plt.draw()
    plt.pause(0.01)

In [ ]:
def place(rock_count = 8, scissor_count = 8, paper_count = 8):
    #create initial clusters roughly equally apart: this was boring
#     rocks = np.repeat([[0,25,0]], rock_count, axis=0)
#     scissors = np.repeat([[-22,-22,1]], scissor_count, axis=0)
#     papers = np.repeat([[22,-22,2]], paper_count, axis=0)
    #create clumps randomly

    loc = np.random.randint(-50, 50, size = [rock_count, 2])
    rocks = np.column_stack((loc, np.zeros(rock_count)))
        
    loc = np.random.randint(-50, 50, size = [scissor_count, 2])
    scissors = np.column_stack((loc, np.zeros(scissor_count)+1))
    
    loc = np.random.randint(-50, 50, size = [paper_count, 2])
    papers = np.column_stack((loc, np.zeros(paper_count)+2))
    
    mass = np.concatenate((rocks, scissors, papers))
    return mass

In [ ]:
def check_bound(x, y, maxX = 50, maxY = 50):
    #check boundaries -maxX ~ maxX, -maxY ~ maxY
    if x >= maxX:
        x = maxX - 5
    elif x <= -maxX:
        x = -maxX + 5
        
    if y >= maxY:
        y = maxY - 5
    elif y <= -maxY:
        y = -maxY + 5
    
    return x, y

In [ ]:
def change(mass):
    for i in range(mass.shape[0]):
        e1 = mass[i]
        for j in range(1, mass.shape[0]):
            e2 = mass[j]
            
            dist = math.dist(e1[:2], e2[:2])
            if dist <= 4:
                if e1[2] == e2[2]:
                    continue
                elif e1[2] == 0:
                    if e2[2] == 1:
                        e2[2] = e1[2]
                    elif e2[2] == 2:
                        e1[2] = e2[2]
                elif e1[2] == 1:
                    if e2[2] == 2:
                        e2[2] = e1[2]
    return mass

In [ ]:
def spock(count= 6):
    loc = np.random.randint(-50, 50, size = [count, 2])
    rocks = np.column_stack((loc, np.zeros(count)))
        
    loc = np.random.randint(-50, 50, size = [count, 2])
    scissors = np.column_stack((loc, np.zeros(count)+1))
    
    loc = np.random.randint(-50, 50, size = [count, 2])
    papers = np.column_stack((loc, np.zeros(count)+2))
    
    loc = np.random.randint(-50, 50, size = [count, 2])
    spock = np.column_stack((loc, np.zeros(count)+3))
    
    loc = np.random.randint(-50, 50, size = [count, 2])
    lizard = np.column_stack((loc, np.zeros(count)+4))
    
    mass = np.concatenate((rocks, scissors, papers, spock, lizard))
    return mass

def lizard(mass):
    for i in range(mass.shape[0]):
        e1 = mass[i]
        for j in range(1, mass.shape[0]):
            e2 = mass[j]
            
            dist = math.dist(e1[:2], e2[:2])
            if dist <= 4:
                if e1[2] == e2[2]:
                    continue
                elif e1[2] == 0:
                    if e2[2] == 1 or e2[2] == 4:
                        e2[2] = e1[2]
                    elif e2[2] == 2 or e2[2] == 3:
                        e1[2] = e2[2]
                    
                elif e1[2] == 1:
                    if e2[2] == 2 or e2[2] == 4:
                        e2[2] = e1[2]
                    elif e2[2] == 3:
                        e1[2] = e2[2]
                elif e1[2] == 2:
                    if e2[2] == 3:
                        e2[2] = e1[2]
                    elif e2[2] == 4:
                        e1[2] = e2[2]
                elif e1[2] == 3:
                    if e2[2] == 4:
                        e1[2] = e2[2]
    return mass

In [ ]:
def nextt(mass, mode = 3):
    new_el = []
    for el in mass:
        x = el[0]
        y = el[1]
        rsp = el[2]
        
        r = np.random.random()
        r2 = np.random.random()
        
        #addition randomness to speed up process
        if r2 >= 0.75:
            j = 3
        else:
            j = 1        
        
        if 0.0 <= r and r < 0.25:
            x -= 2*j
        elif 0.25 <= r and r < 0.5:
            x += 2*j
        elif 0.5 <= r and r < 0.75:
            y -= 2*j
        else:
            y += 2*j
            
        x, y = check_bound(x, y)
        
        new_el.append(np.array([x, y, rsp]))
        
    new_el = np.array(new_el)
    
    if mode == 3:
        new_el = change(new_el)
    elif mode == 5:
        new_el = lizard(new_el)
    return new_el

In [ ]:
def single(mass):
    if len(np.unique(mass[:,2])) == 1:
        return True
    else:
        return False

In [ ]:
#run simulation
mass = place()

fig = init_figure()
display(mass)
t = 0
with writer.saving(fig, "animation1.mp4", dpi=200):
    
    while t < 3000:
        writer.grab_frame()
        mass = nextt(mass)
        
        if single(mass):
            break
            
        t += 1
        
        display(mass)

In [ ]:
#run simulation
mass = spock()

fig = init_figure()
display(mass, 5)
t = 0
with writer.saving(fig, "animation2.mp4", dpi=200):
    
    while t < 3000:
        writer.grab_frame()
        mass = nextt(mass, 5)
        
        if single(mass):
            break
            
        t += 1
        
        display(mass, 5)